In [1]:
import pandas as pd
import seaborn as sns
import numpy as np
import sqlalchemy
import plotly.express as px
import dash
import dash_core_components as dcc
import dash_html_components as html
from jupyter_dash import JupyterDash
from dash.dependencies import Input, Output
from sqlalchemy import create_engine

In [2]:
# Follows django database settings format, replace with your own settings
DATABASES = {
    'hoss_db':{
        'NAME': 'hoss_db',
        'USER': 'dev_user',
        'PASSWORD': 'RRpBdDusLaTN2Uoo',
        'HOST': 'hoss-db.cluster-cx3tki3wuuoj.us-east-1.rds.amazonaws.com',
        'PORT': 5432,
    },
}

# Choose the database to use
db = DATABASES['hoss_db']

# Construct an engine connection string
engine_string = "postgresql+psycopg2://{user}:{password}@{host}:{port}/{database}".format(
    user = db['USER'],
    password = db['PASSWORD'],
    host = db['HOST'],
    port = db['PORT'],
    database = db['NAME'],
)

# Create sqlalchemy engine
engine = create_engine(engine_string)

# SQL query
query= '''SELECT join_account.Account_ID AS Account_ID, Account_UUID, Account_Name, Account_Email, join_account.Created_at, Plan_ID, Plan_Name, Date, Requests
               FROM
                      (SELECT accounts.id AS Account_ID,
                              accounts.uuid AS Account_UUID,
                              account_versions.name AS Account_Name,
                              accounts.created_at AS Created_at
                       FROM accounts
                       JOIN ( SELECT DISTINCT ON (account_id) account_id, name
                              FROM account_versions
                              ORDER BY account_id, id DESC
                        ) account_versions
                        ON accounts.id = account_versions.account_id
                      ) AS join_account
                  JOIN
                      (SELECT DISTINCT ON (account_id) account_id, id,
                              user_versions.email AS Account_Email
                       FROM users
                       JOIN ( SELECT DISTINCT ON (user_id) user_id, email
                              FROM user_versions
                              ORDER BY user_id, id DESC
                        ) user_versions
                       ON users.id = user_versions.user_id
                       ORDER BY account_id, id
                      ) AS join_user
                        ON join_account.Account_ID = join_user.account_id
                  JOIN
                      (SELECT plan_versions.plan_id AS Plan_ID,
                              plan_versions.name AS Plan_Name,
                              subscriptions.account_id
                       FROM plans
                       JOIN (SELECT DISTINCT ON (plan_id) plan_id, name
                             FROM plan_versions
                             ORDER BY plan_id, id DESC
                       ) plan_versions
                       ON plans.id = plan_versions.plan_id
                       JOIN (SELECT DISTINCT ON (account_id) account_id, plan_id
                             FROM subscriptions
                             ORDER BY account_id, plan_id DESC
                           ) subscriptions
                       ON plans.id = subscriptions.plan_id
                      ) AS join_plan_sub
                        ON join_account.Account_ID = join_plan_sub.account_id
                  JOIN
                      report_daily_usage
                      ON join_account.Account_ID = report_daily_usage.account_id
            ORDER BY account_id, date DESC
            '''

# Read a table from database into pandas dataframe
df = pd.read_sql_query(query, engine)
df['date'] = pd.to_datetime(df['date']).dt.strftime('%m/%d/%y')
df['created_at'] = pd.to_datetime(df['created_at']).dt.strftime('%m/%d/%y')

In [3]:
# Filter necessary columns
df1= df[['account_id', 'account_name','created_at', 'plan_name', 'date','requests']]

# Replace NA values in "account_name" with its "NA" string
pd.options.mode.chained_assignment = None #Turn off warning
df1._update_inplace=df1['account_name'].fillna('NA', inplace= True)

# Pivot the df1 dataframe to get a desired format
daily_request= df1.pivot_table(index=['account_id','account_name','created_at','plan_name'], 
                               columns=['date'], values=['requests'])

# Sort the table by descending requests 
daily_request['total_request']= daily_request.sum(axis= 1)
daily_request_sorted= daily_request.sort_values(by= ['total_request'], ascending= False)

# Create new df for the bar chart
df3= daily_request_sorted.reset_index()
df3['account_id_name']= df3['account_id'].astype(str).str.cat(df3['account_name'], sep = '_') # Create new column combines account_id and account_name
df3.insert(2, 'account_id_name', df3['account_id_name'], allow_duplicates=True) # Move column account_id_name to the third location
df3 = df3.loc[:,~df3.columns.duplicated()] 
df3['Jan_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('01')].sum(axis= 1) # Calculate total request for each month
df3['Feb_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('02')].sum(axis= 1) # need to use get_level_values cause we have multi index
df3['Mar_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('03')].sum(axis= 1)
df3['Apr_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('04')].sum(axis= 1)
df3['May_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('05')].sum(axis= 1)
df3['Jun_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('06')].sum(axis= 1)
df3['Jul_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('07')].sum(axis= 1)
df3['Aug_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('08')].sum(axis= 1)
df3['Sep_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('09')].sum(axis= 1)
df3['Oct_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('10')].sum(axis= 1)
df3['Nov_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('11')].sum(axis= 1)
df3['Dec_request'] = df3.loc[:, df3.columns.get_level_values(1).str.startswith('12')].sum(axis= 1)
df3.drop(df3.filter(regex= '1|2|3|4|5|6|7|8|9|10|11|12' , axis= 1), axis=1, inplace= True) # Drop daily request

# Hightlight the result with color palette (replace/highlight NA with blank str/white color)
cm = sns.light_palette('green', as_cmap=True)
table = daily_request_sorted.style.background_gradient(cmap=cm, axis=1,subset= daily_request_sorted.columns[0:-1])\
.highlight_null(null_color='white')\
.format('{0:,.0f}',na_rep= '')\
.set_caption('No. of daily request by Account')\
.set_table_styles([{
    'selector': 'caption',
    'props': [('color', 'black'), ('font-size', '18px')]}])\
.set_properties(**{'border-color': 'black','text-align': 'center','border-width':'thin','border-style':'dotted'})
table

In [4]:
# Create the pie chart
pie = px.pie(df3, values= df3['plan_name'].value_counts(), 
             names= df3['plan_name'].value_counts().index.to_list(),
             labels={'names': 'account_plan'},
             title='Proportion of account_plan')
pie.update_traces(textposition='outside', textfont_size=13,
                 texttemplate = '"%{label}": %{value} <br>(%{percent})')
pie.update_layout(legend_title_text='account_plan', legend={'traceorder':'reversed'})

# Create the 'No. of account created by month' bar chart
bar1 = px.bar(df3, x= pd.to_datetime(df3['created_at']).dt.strftime('%m/%y').sort_values(ascending= True).unique().tolist(),
               y= df3.groupby(pd.to_datetime(df3['created_at']).dt.strftime('%m/%y')).size().sort_index(ascending= True))
bar1.update_layout(
    title='No. of account created by month',
    xaxis_title= 'Month',
    yaxis_title= 'No. of account created',
    yaxis = dict(showgrid= True, gridwidth= 1)
    )
bar1.update_xaxes(type='category')
bar1.update_traces(texttemplate='%{value:.2}', textposition='outside')

# Create DASH app
external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

app = dash.Dash(__name__, external_stylesheets=external_stylesheets)

app.layout = html.Div([
    html.Div([
    html.H1(children='Daily Report Dashboard'),
    
    html.Label('Select a month'),
    dcc.Dropdown(id= 'choose_month',
    options=[
        {'label': 'All', 'value': 'total_request'},
        {'label': 'January', 'value': 'Jan_request'},
        {'label': 'Febuary', 'value': 'Feb_request'},
        {'label': 'March', 'value': 'Mar_request'},
        {'label': 'April', 'value': 'Apr_request'},
        {'label': 'May', 'value': 'May_request'},
        {'label': 'June', 'value': 'Jun_request'},
        {'label': 'July', 'value': 'Jul_request'},
        {'label': 'August', 'value': 'Aug_request'},
        {'label': 'September', 'value': 'Sep_request'},
        {'label': 'October', 'value': 'Oct_request'},
        {'label': 'November', 'value': 'Nov_request'},
        {'label': 'December', 'value': 'Dec_request'}
    ],
    value= 'total_request',
    multi= False,
    clearable= False,
    style= {'width':'30%'}
    ),
    
    dcc.Graph(id='bar_chart')
             ]),
     
    html.Div([
    dcc.Graph(
        id='pie',
        figure= pie),
    
    dcc.Graph(
        id='bar1',
        figure= bar1)
            ], style= { 'columnCount': '2'})
])


@app.callback(
    Output(component_id='bar_chart', component_property='figure'),
    [Input(component_id='choose_month', component_property='value')]
)
def update_barchart(select_month):
    new_df= df3
    barchart= px.bar(new_df, x= new_df[select_month],
                     y= new_df['account_id_name'],
                     color= new_df['plan_name'],
                     color_discrete_map={'Free':'#636EFA',
                                         'Hoss Plus':'#EF553B'},
                     height= (len(df3)) * 20,
                     orientation= 'h',
                     text= new_df[select_month])\
                     .update_yaxes(categoryorder="total ascending")
  
    barchart.update_layout(title='No. of requests by account',
                           legend_title= 'account_plan', showlegend= True,
                           xaxis_title= 'No. of requests',
                           yaxis_title= 'account_id_name',
                           yaxis = dict(tickmode = 'auto'),
                           xaxis = dict(showgrid= True, gridwidth= 1, nticks= 10))
    
    barchart.update_traces(texttemplate='%{text:.2s}', textposition='outside')
      
    return barchart

if __name__ == '__main__':
    app.run_server(debug=False, port= 2000) #Change port= 8000, 9000, etc. in case you encounter [Errno 48] Address already in use
                                            #Change debug=True if you don't use Jupyter for the ability to auto reload dashboard in case the above code changed

Dash is running on http://127.0.0.1:2000/

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:2000/ (Press CTRL+C to quit)
127.0.0.1 - - [13/Oct/2020 13:49:12] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [13/Oct/2020 13:49:12] "GET /_dash-component-suites/dash_renderer/react@16.v1_1_2m1576595738.8.6.min.js HTTP/1.1" 200 -
127.0.0.1 - - [13/Oct/2020 13:49:12] "GET /_dash-component-suites/dash_renderer/prop-types@15.v1_1_2m1576595738.7.2.min.js HTTP/1.1" 200 -
127.0.0.1 - - [13/Oct/2020 13:49:12] "GET /_dash-component-suites/dash_core_components/highlight.v1_3_1m1576595950.pack.js HTTP/1.1" 200 -
127.0.0.1 - - [13/Oct/2020 13:49:13] "GET /_dash-component-suites/dash_html_components/dash_html_components.v1_0_1m1576596177.min.js HTTP/1.1" 200 -
127.0.0.1 - - [13/Oct/2020 13:49:13] "GET /_dash-component-suites/dash_renderer/react-dom@16.v1_1_2m1576595738.8.6.min.js HTTP/1.1" 200 -
127.0.0.1 - - [13/Oct/2020 13:49:13] "GET /_dash-component-suites/dash_renderer/dash_renderer.v1_1_2m1576595738.min.js HTTP/1.1" 200 -
127.0.0.1 - - [13/Oct/2020 13:49:13] "GET /_da

In [14]:
import dash_pivottable

app1 = dash.Dash(__name__)
server = app1.server

app1.layout = html.Div(
    dash_pivottable.PivotTable(data= df1.reset_index().to_dict('rows'),
        cols=['dates'],
        rows=['account_name'],
        vals=['requests']
    )
)

if __name__ == "__main__":
    app1.run_server(debug=False)

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


OSError: [Errno 9] Bad file descriptor

In [13]:
df1.reset_index().to_dict('rows')

[{'index': 0,
  'account_id': 1,
  'account_name': 'Hoss Dev',
  'created_at': '05/26/20',
  'plan_name': 'Hoss Plus',
  'date': '08/17/20',
  'requests': 5420},
 {'index': 1,
  'account_id': 1,
  'account_name': 'Hoss Dev',
  'created_at': '05/26/20',
  'plan_name': 'Hoss Plus',
  'date': '08/16/20',
  'requests': 5316},
 {'index': 2,
  'account_id': 1,
  'account_name': 'Hoss Dev',
  'created_at': '05/26/20',
  'plan_name': 'Hoss Plus',
  'date': '08/15/20',
  'requests': 5301},
 {'index': 3,
  'account_id': 1,
  'account_name': 'Hoss Dev',
  'created_at': '05/26/20',
  'plan_name': 'Hoss Plus',
  'date': '08/14/20',
  'requests': 5289},
 {'index': 4,
  'account_id': 1,
  'account_name': 'Hoss Dev',
  'created_at': '05/26/20',
  'plan_name': 'Hoss Plus',
  'date': '08/13/20',
  'requests': 5315},
 {'index': 5,
  'account_id': 1,
  'account_name': 'Hoss Dev',
  'created_at': '05/26/20',
  'plan_name': 'Hoss Plus',
  'date': '08/12/20',
  'requests': 5871},
 {'index': 6,
  'account_id'